In [7]:
import os
import numpy as np
import pandas as pd
import xgboost as xgb
import datetime
from xgboost import plot_importance, plot_tree
from sklearn.metrics import mean_squared_error as MSE
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import PredefinedSplit

In [8]:
def lag(data, dic):
    cols = []
    for key, value in dic.items():
        for i in range(1, value+1):
            cols.append(data[key].shift(i).rename('{}_lag{}'.format(data[key].name, i)))
    return pd.concat([data["date"],data["Adj_Close_BTC-USD"]] + cols, axis = 1)

# Regression Model (with Sentiment)

### Baseline Model

In [9]:
feature_lags = {"Adj_Close_BTC-USD" : 1, 
                "Adj_Close_SPY" : 1,
                "Adj_Close_GLD" : 1,
                "Adj_Close_CHFUSD=X" : 1,
                "Adj_Close_EURUSD=X" : 1,
                "Adj_Close_GBPUSD=X" : 1,
                "Adj_Close_JPYUSD=X" : 1,
                "blockchain_transactions_per_block" : 1,
                "blockchain_hash_rates" : 1,
                "coindesk_sentiment" : 1,
                "reddit_comments_sentiments" : 1,
                "top_50_reddit_posts_sentiments" : 1}

df = pd.read_csv("../../data/cooked_data/cooked_complete_dataset_growing_2.csv")
df.dropna(inplace = True)
df['date'] = df['date'].apply(lambda x: datetime.datetime.strptime(x, "%d/%m/%y"))
df["date"] = pd.to_datetime(df["date"], format='%d/%m/%Y', infer_datetime_format=True)

df = lag(df, feature_lags)

refit = df[(df["date"] >= "2021-01-01") & (df["date"] <= "2021-03-29")]
full = df.copy(deep = True)

train = df[(df["date"] >= "2021-01-01") & (df["date"] <= "2021-03-14")]
validation = df[(df["date"] > "2021-03-14") & (df['date'] <= '2021-03-29')]
test = df[(df["date"] > "2021-03-29") & (df["date"] <= "2021-04-12")]

x_train = train.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_train = train["Adj_Close_BTC-USD"]

x_validation = validation.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_validation = validation["Adj_Close_BTC-USD"]

x_test = test.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_test = test["Adj_Close_BTC-USD"]

x_full = full.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_full = full["Adj_Close_BTC-USD"]

In [10]:
print("X train shape: ",x_train.shape)
print("y train shape: ",y_train.shape)

print("X val shape: ",x_validation.shape)
print("y val shape: ",y_validation.shape)

print("X test shape: ",x_test.shape)
print("y test shape: ",y_test.shape)

print("X full shape: ",x_full.shape)
print("y full shape: ",y_full.shape)

X train shape:  (73, 12)
y train shape:  (73,)
X val shape:  (15, 12)
y val shape:  (15,)
X test shape:  (14, 12)
y test shape:  (14,)
X full shape:  (121, 12)
y full shape:  (121,)


In [11]:
sc = MinMaxScaler(feature_range = (0, 1))
sc.fit(x_train)
x_train_trans = sc.transform(x_train)
x_validation_trans = sc.transform(x_validation)
x_test_trans = sc.transform(x_test)

In [12]:
eval_set = [(x_validation_trans, y_validation)]


xgb_r = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators = 20, seed = 123)
xgb_r.fit(x_train_trans, y_train, early_stopping_rounds=10, eval_set=eval_set)
y_pred = xgb_r.predict(x_test_trans)

# RMSE Computation
rmse = np.sqrt(MSE(y_test, y_pred))
print("RMSE : % f" %(rmse))

[0]	validation_0-rmse:41318.83594
Will train until validation_0-rmse hasn't improved in 10 rounds.
[1]	validation_0-rmse:31026.32031
[2]	validation_0-rmse:24239.49609
[3]	validation_0-rmse:18526.16016
[4]	validation_0-rmse:13808.79394
[5]	validation_0-rmse:10221.01269
[6]	validation_0-rmse:7617.16309
[7]	validation_0-rmse:5644.21777
[8]	validation_0-rmse:4243.82812
[9]	validation_0-rmse:3512.00317
[10]	validation_0-rmse:3061.44580
[11]	validation_0-rmse:2803.42822
[12]	validation_0-rmse:2437.04639
[13]	validation_0-rmse:2257.31934
[14]	validation_0-rmse:2159.86938
[15]	validation_0-rmse:2126.34546
[16]	validation_0-rmse:2119.06592
[17]	validation_0-rmse:2143.95947
[18]	validation_0-rmse:2180.40747
[19]	validation_0-rmse:2223.01465
RMSE :  2889.696990


### Hyperparemeter Tuning

In [13]:
# setting default parameters

eval_set = [(x_validation_trans, y_validation)]

parameters = {
    "learning_rate": [0.05, 0.10, 0.15 ],
 "max_depth"        : [ 3, 4, 5, 6, 8,],
 "min_child_weight" : [ 1, 3, 5, 7 ],
 "gamma"            : [ 0.0, 0.1, 0.2 ],
 "colsample_bytree" : [ 0.3, 0.4, 0.5] }

split_index = [-1] * x_train.shape[0] + [0] * x_validation.shape[0]

pds = PredefinedSplit(test_fold=split_index)

model = xgb.XGBRegressor(eval_metric="rmse", objective='reg:squarederror', verbose=False)

clf = GridSearchCV(estimator=model, 
                   cv=pds,
                   param_grid=parameters)

clf.fit(np.concatenate((x_train_trans, x_validation_trans)), np.concatenate((y_train, y_validation)), early_stopping_rounds=10, eval_set=eval_set)

print(f'Best params: {clf.best_params_}')
print(f'Best validation score = {clf.best_score_}')

[18:32:38] WARNING: C:\Users\Administrator\workspace\xgboost-win64_release_1.2.0\src\learner.cc:516: 
Parameters: { verbose } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[0]	validation_0-rmse:53792.88281
Will train until validation_0-rmse hasn't improved in 10 rounds.
[1]	validation_0-rmse:51431.41016
[2]	validation_0-rmse:49313.28906
[3]	validation_0-rmse:47248.24219
[4]	validation_0-rmse:45283.98828
[5]	validation_0-rmse:43334.17969
[6]	validation_0-rmse:41487.48438
[7]	validation_0-rmse:39850.76953
[8]	validation_0-rmse:38227.98438
[9]	validation_0-rmse:36692.67969
[10]	validation_0-rmse:35183.14844
[11]	validation_0-rmse:33738.05859
[12]	validation_0-rmse:32366.23633
[13]	validation_0-rmse:31061.24023
[14]	validation_0-rmse:29806.63281
[15]	validation_0-rmse:28726.97266


[1]	validation_0-rmse:51431.41016
[2]	validation_0-rmse:49313.28906
[3]	validation_0-rmse:47248.24219
[4]	validation_0-rmse:45283.98828
[5]	validation_0-rmse:43334.17969
[6]	validation_0-rmse:41487.48438
[7]	validation_0-rmse:39850.76953
[8]	validation_0-rmse:38227.98438
[9]	validation_0-rmse:36692.67969
[10]	validation_0-rmse:35183.14844
[11]	validation_0-rmse:33738.05859
[12]	validation_0-rmse:32366.23633
[13]	validation_0-rmse:31061.24023
[14]	validation_0-rmse:29806.63281
[15]	validation_0-rmse:28726.97266
[16]	validation_0-rmse:27701.04492
[17]	validation_0-rmse:26726.25391
[18]	validation_0-rmse:25694.68555
[19]	validation_0-rmse:24683.14258
[20]	validation_0-rmse:23759.76758
[21]	validation_0-rmse:22878.96094
[22]	validation_0-rmse:22105.78906
[23]	validation_0-rmse:21238.91016
[24]	validation_0-rmse:20548.91016
[25]	validation_0-rmse:19794.66602
[26]	validation_0-rmse:19077.03516
[27]	validation_0-rmse:18245.92188
[28]	validation_0-rmse:17453.78320
[29]	validation_0-rmse:16698.

[14]	validation_0-rmse:29806.63281
[15]	validation_0-rmse:28726.97266
[16]	validation_0-rmse:27701.04492
[17]	validation_0-rmse:26726.25391
[18]	validation_0-rmse:25694.68555
[19]	validation_0-rmse:24683.14258
[20]	validation_0-rmse:23759.76758
[21]	validation_0-rmse:22878.96094
[22]	validation_0-rmse:22105.78906
[23]	validation_0-rmse:21238.91016
[24]	validation_0-rmse:20548.91016
[25]	validation_0-rmse:19794.66602
[26]	validation_0-rmse:19077.03516
[27]	validation_0-rmse:18245.92188
[28]	validation_0-rmse:17453.78320
[29]	validation_0-rmse:16698.82422
[30]	validation_0-rmse:16023.02930
[31]	validation_0-rmse:15334.33887
[32]	validation_0-rmse:14678.07617
[33]	validation_0-rmse:14133.87598
[34]	validation_0-rmse:13664.06836
[35]	validation_0-rmse:13227.84961
[36]	validation_0-rmse:12676.33398
[37]	validation_0-rmse:12150.96680
[38]	validation_0-rmse:11667.27246
[39]	validation_0-rmse:11141.07812
[40]	validation_0-rmse:10800.33398
[41]	validation_0-rmse:10429.24609
[42]	validation_0-rm

[27]	validation_0-rmse:18245.92188
[28]	validation_0-rmse:17453.78320
[29]	validation_0-rmse:16698.82422
[30]	validation_0-rmse:16023.02930
[31]	validation_0-rmse:15334.30762
[32]	validation_0-rmse:14678.01465
[33]	validation_0-rmse:14133.82519
[34]	validation_0-rmse:13666.70898
[35]	validation_0-rmse:13230.63379
[36]	validation_0-rmse:12679.06836
[37]	validation_0-rmse:12153.65332
[38]	validation_0-rmse:11669.60938
[39]	validation_0-rmse:11143.45215
[40]	validation_0-rmse:10753.50781
[41]	validation_0-rmse:10381.09473
[42]	validation_0-rmse:9912.10352
[43]	validation_0-rmse:9464.03711
[44]	validation_0-rmse:9075.75293
[45]	validation_0-rmse:8665.22754
[46]	validation_0-rmse:8396.03711
[47]	validation_0-rmse:8018.38428
[48]	validation_0-rmse:7799.62793
[49]	validation_0-rmse:7452.50195
[50]	validation_0-rmse:7121.41992
[51]	validation_0-rmse:6816.78320
[52]	validation_0-rmse:6515.06494
[53]	validation_0-rmse:6230.81250
[54]	validation_0-rmse:6035.59277
[55]	validation_0-rmse:5796.31738

[40]	validation_0-rmse:10800.33398
[41]	validation_0-rmse:10429.24609
[42]	validation_0-rmse:9960.17090
[43]	validation_0-rmse:9512.03223
[44]	validation_0-rmse:9092.22266
[45]	validation_0-rmse:8683.06445
[46]	validation_0-rmse:8413.14062
[47]	validation_0-rmse:8036.78711
[48]	validation_0-rmse:7809.13623
[49]	validation_0-rmse:7463.18213
[50]	validation_0-rmse:7133.22852
[51]	validation_0-rmse:6830.32959
[52]	validation_0-rmse:6529.61475
[53]	validation_0-rmse:6222.57178
[54]	validation_0-rmse:6017.95020
[55]	validation_0-rmse:5792.37256
[56]	validation_0-rmse:5551.66797
[57]	validation_0-rmse:5337.12549
[58]	validation_0-rmse:5130.11914
[59]	validation_0-rmse:4949.89404
[60]	validation_0-rmse:4769.30078
[61]	validation_0-rmse:4634.80566
[62]	validation_0-rmse:4448.09228
[63]	validation_0-rmse:4278.12353
[64]	validation_0-rmse:4122.20898
[65]	validation_0-rmse:3956.37476
[66]	validation_0-rmse:3828.09619
[67]	validation_0-rmse:3684.68921
[68]	validation_0-rmse:3549.46143
[69]	validat

...

[7]	validation_0-rmse:19988.83594
[8]	validation_0-rmse:18051.69922
[9]	validation_0-rmse:16243.85938
[10]	validation_0-rmse:14197.07422
[11]	validation_0-rmse:12291.95606
[12]	validation_0-rmse:10691.48535
[13]	validation_0-rmse:9342.74023
[14]	validation_0-rmse:8073.39453
[15]	validation_0-rmse:6977.95068
[16]	validation_0-rmse:6036.01855
[17]	validation_0-rmse:5279.39404
[18]	validation_0-rmse:4559.82666
[19]	validation_0-rmse:4087.31787
[20]	validation_0-rmse:3598.52393
[21]	validation_0-rmse:3313.38110
[22]	validation_0-rmse:2975.42676
[23]	validation_0-rmse:2679.80151
[24]	validation_0-rmse:2417.99658
[25]	validation_0-rmse:2232.24683
[26]	validation_0-rmse:2127.94971
[27]	validation_0-rmse:2073.25415
[28]	validation_0-rmse:2023.85474
[29]	validation_0-rmse:1953.70203
[30]	validation_0-rmse:1912.66235
[31]	validation_0-rmse:1897.29004
[32]	validation_0-rmse:1902.60657
[33]	validation_0-rmse:1921.33716
[34]	validation_0-rmse:1937.13330
[35]	validation_0-rmse:1975.56397
[36]	valida

[15]	validation_0-rmse:6977.95068
[16]	validation_0-rmse:6036.01855
[17]	validation_0-rmse:5278.85596
[18]	validation_0-rmse:4557.64502
[19]	validation_0-rmse:4070.36499
[20]	validation_0-rmse:3714.64258
[21]	validation_0-rmse:3316.77515
[22]	validation_0-rmse:2968.63721
[23]	validation_0-rmse:2682.95703
[24]	validation_0-rmse:2446.83691
[25]	validation_0-rmse:2259.27124
[26]	validation_0-rmse:2123.96484
[27]	validation_0-rmse:1999.66882
[28]	validation_0-rmse:1950.94067
[29]	validation_0-rmse:1926.84949
[30]	validation_0-rmse:1902.45740
[31]	validation_0-rmse:1899.40283
[32]	validation_0-rmse:1882.18091
[33]	validation_0-rmse:1902.84009
[34]	validation_0-rmse:1941.41162
[35]	validation_0-rmse:1938.71680
[36]	validation_0-rmse:1939.34009
[37]	validation_0-rmse:1939.30957
[38]	validation_0-rmse:1952.79785
[39]	validation_0-rmse:1969.57947
[40]	validation_0-rmse:1989.95947
[41]	validation_0-rmse:2001.43933
[42]	validation_0-rmse:2014.34961
Stopping. Best iteration:
[32]	validation_0-rmse

[19]	validation_0-rmse:4066.38696
[20]	validation_0-rmse:3701.32739
[21]	validation_0-rmse:3389.12622
[22]	validation_0-rmse:3035.44238
[23]	validation_0-rmse:2747.25146
[24]	validation_0-rmse:2511.19873
[25]	validation_0-rmse:2321.42773
[26]	validation_0-rmse:2182.52710
[27]	validation_0-rmse:2074.74707
[28]	validation_0-rmse:2035.66333
[29]	validation_0-rmse:1967.50598
[30]	validation_0-rmse:1930.14490
[31]	validation_0-rmse:1923.78101
[32]	validation_0-rmse:1902.26160
[33]	validation_0-rmse:1917.32544
[34]	validation_0-rmse:1937.68127
[35]	validation_0-rmse:1929.77087
[36]	validation_0-rmse:1927.66736
[37]	validation_0-rmse:1929.12732
[38]	validation_0-rmse:1923.03992
[39]	validation_0-rmse:1931.94238
[40]	validation_0-rmse:1947.38538
[41]	validation_0-rmse:1959.56006
[42]	validation_0-rmse:1958.88806
Stopping. Best iteration:
[32]	validation_0-rmse:1902.26160

[18:34:00] WARNING: C:\Users\Administrator\workspace\xgboost-win64_release_1.2.0\src\learner.cc:516: 
Parameters: { verbose

[20]	validation_0-rmse:3740.97119
[21]	validation_0-rmse:3332.19849
[22]	validation_0-rmse:2980.79199
[23]	validation_0-rmse:2692.26904
[24]	validation_0-rmse:2480.92700
[25]	validation_0-rmse:2306.51221
[26]	validation_0-rmse:2182.12769
[27]	validation_0-rmse:2062.79175
[28]	validation_0-rmse:2020.43042
[29]	validation_0-rmse:1959.25488
[30]	validation_0-rmse:1920.70361
[31]	validation_0-rmse:1907.46252
[32]	validation_0-rmse:1862.44665
[33]	validation_0-rmse:1853.35059
[34]	validation_0-rmse:1878.71814
[35]	validation_0-rmse:1875.57214
[36]	validation_0-rmse:1879.07788
[37]	validation_0-rmse:1894.09143
[38]	validation_0-rmse:1904.19495
[39]	validation_0-rmse:1918.45666
[40]	validation_0-rmse:1934.09351
[41]	validation_0-rmse:1948.55115
[42]	validation_0-rmse:1962.86523
[43]	validation_0-rmse:1974.54102
Stopping. Best iteration:
[33]	validation_0-rmse:1853.35059

[18:34:00] WARNING: C:\Users\Administrator\workspace\xgboost-win64_release_1.2.0\src\learner.cc:516: 
Parameters: { verbose

[21]	validation_0-rmse:2475.77930
[22]	validation_0-rmse:2175.99707
[23]	validation_0-rmse:1982.78906
[24]	validation_0-rmse:1794.66138
[25]	validation_0-rmse:1630.11047
[26]	validation_0-rmse:1493.90955
[27]	validation_0-rmse:1381.33704
[28]	validation_0-rmse:1295.53235
[29]	validation_0-rmse:1209.70874
[30]	validation_0-rmse:1131.30920
[31]	validation_0-rmse:1078.74475
[32]	validation_0-rmse:1050.04834
[33]	validation_0-rmse:990.19257
[34]	validation_0-rmse:972.68829
[35]	validation_0-rmse:962.21252
[36]	validation_0-rmse:952.38568
[37]	validation_0-rmse:932.70898
[38]	validation_0-rmse:922.26208
[39]	validation_0-rmse:917.04163
[40]	validation_0-rmse:874.59424
[41]	validation_0-rmse:855.37366
[42]	validation_0-rmse:852.95746
[43]	validation_0-rmse:857.10211
[44]	validation_0-rmse:824.44305
[45]	validation_0-rmse:814.46387
[46]	validation_0-rmse:782.57056
[47]	validation_0-rmse:768.29047
[48]	validation_0-rmse:748.42767
[49]	validation_0-rmse:750.45978
[50]	validation_0-rmse:732.2938

In [14]:
model = xgb.XGBRegressor(**clf.best_params_, objective='reg:squarederror')
model.fit(x_train_trans, y_train, verbose=False, early_stopping_rounds=10, eval_set=eval_set)

y_train_pred = model.predict(x_train_trans)

# Train Set RMSE Computation
rmse = np.sqrt(MSE(y_train, y_train_pred))
print("Train set RMSE: % f" %(rmse))

y_pred = model.predict(x_test_trans)

# Test Set RMSE Computation
rmse = np.sqrt(MSE(y_test, y_pred))
print("Test set RMSE: % f" %(rmse))

Train set RMSE:  823.334328
Test set RMSE:  3081.769493


In [15]:
# with sentiments 
y_train_pred = model.predict(x_train_trans)
y_validation_pred = model.predict(x_validation_trans)
y_test_pred = model.predict(x_test_trans)

concat = np.concatenate((y_train_pred, y_validation_pred, y_test_pred))
concat.shape

pd.DataFrame(concat).to_csv(r'C:\Users\Yi Hao\Desktop\XGBoost_regression_with_sentiment.csv')

# Regression Model (without Sentiment)

### Baseline Model

In [16]:
feature_lags = {"Adj_Close_BTC-USD" : 1,
                "Adj_Close_SPY" : 1,
                "Adj_Close_GLD" : 1,
                "Adj_Close_CHFUSD=X" : 1,
                "Adj_Close_EURUSD=X" : 1,
                "Adj_Close_GBPUSD=X" : 1,
                "Adj_Close_JPYUSD=X" : 1,
                "blockchain_transactions_per_block" : 1,
                "blockchain_hash_rates" : 1}

df = pd.read_csv("../../data/cooked_data/cooked_complete_dataset_growing_2.csv")
df.dropna(inplace = True)
df['date'] = df['date'].apply(lambda x: datetime.datetime.strptime(x, "%d/%m/%y"))
df["date"] = pd.to_datetime(df["date"], format='%d/%m/%Y', infer_datetime_format=True)

df = lag(df, feature_lags)

refit = df[(df["date"] >= "2021-01-01") & (df["date"] <= "2021-03-29")]
full = df.copy(deep = True)

sentiment_reg = df[df["date"] >= "1/1/2021"]

train = df[(df["date"] >= "2021-01-01") & (df["date"] <= "2021-03-14")]
validation = df[(df["date"] > "2021-03-14") & (df['date'] <= '2021-03-29')]
test = df[(df["date"] > "2021-03-29") & (df["date"] <= "2021-04-12")]

x_train = train.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_train = train["Adj_Close_BTC-USD"]

x_validation = validation.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_validation = validation["Adj_Close_BTC-USD"]

x_test = test.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_test = test["Adj_Close_BTC-USD"]

x_full = full.drop(["date", "Adj_Close_BTC-USD"], axis = 1)
y_full = full["Adj_Close_BTC-USD"]

In [17]:
sc = MinMaxScaler(feature_range = (0, 1))
sc.fit(x_train)
x_train_trans = sc.transform(x_train)
x_validation_trans = sc.transform(x_validation)
x_test_trans = sc.transform(x_test)

In [18]:
eval_set = [(x_validation_trans, y_validation)]

xgb_r = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators = 20, seed = 123)
xgb_r.fit(x_train_trans, y_train, early_stopping_rounds=10, eval_set=eval_set)
y_pred = xgb_r.predict(x_test_trans)

# RMSE Computation
rmse = np.sqrt(MSE(y_test, y_pred))
print("RMSE : % f" %(rmse))

[0]	validation_0-rmse:41318.83594
Will train until validation_0-rmse hasn't improved in 10 rounds.
[1]	validation_0-rmse:31026.32031
[2]	validation_0-rmse:24239.49609
[3]	validation_0-rmse:18526.16016
[4]	validation_0-rmse:13808.79394
[5]	validation_0-rmse:10221.01269
[6]	validation_0-rmse:7625.88770
[7]	validation_0-rmse:5641.14551
[8]	validation_0-rmse:4251.13916
[9]	validation_0-rmse:3522.93750
[10]	validation_0-rmse:2926.88330
[11]	validation_0-rmse:2450.86597
[12]	validation_0-rmse:2194.24878
[13]	validation_0-rmse:2107.39404
[14]	validation_0-rmse:2101.62622
[15]	validation_0-rmse:2175.54883
[16]	validation_0-rmse:2262.26807
[17]	validation_0-rmse:2323.56519
[18]	validation_0-rmse:2418.78638
[19]	validation_0-rmse:2501.19678
RMSE :  2945.941112


### Hyperparemeter Tuning

In [19]:
# setting default parameters

eval_set = [(x_validation_trans, y_validation)]

parameters = {
    "learning_rate": [0.05, 0.10, 0.15 ],
 "max_depth"        : [ 3, 4, 5, 6, 8,],
 "min_child_weight" : [ 1, 3, 5, 7 ],
 "gamma"            : [ 0.0, 0.1, 0.2 ],
 "colsample_bytree" : [ 0.3, 0.4, 0.5] }

split_index = [-1] * x_train.shape[0] + [0] * x_validation.shape[0]

pds = PredefinedSplit(test_fold=split_index)

model = xgb.XGBRegressor(eval_metric="rmse", objective='reg:squarederror', verbose=False)

clf = GridSearchCV(estimator=model, 
                   cv=pds,
                   param_grid=parameters)

clf.fit(np.concatenate((x_train_trans, x_validation_trans)), np.concatenate((y_train, y_validation)), early_stopping_rounds=10, eval_set=eval_set)

print(f'Best params: {clf.best_params_}')
print(f'Best validation score = {clf.best_score_}')

[18:34:01] WARNING: C:\Users\Administrator\workspace\xgboost-win64_release_1.2.0\src\learner.cc:516: 
Parameters: { verbose } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[0]	validation_0-rmse:53792.88281
Will train until validation_0-rmse hasn't improved in 10 rounds.
[1]	validation_0-rmse:51431.41016
[2]	validation_0-rmse:49313.28906
[3]	validation_0-rmse:47316.29297
[4]	validation_0-rmse:45267.60156
[5]	validation_0-rmse:43318.59375
[6]	validation_0-rmse:41472.67969
[7]	validation_0-rmse:39797.48438
[8]	validation_0-rmse:38219.58594
[9]	validation_0-rmse:36793.48047
[10]	validation_0-rmse:35411.99609
[11]	validation_0-rmse:34009.18359
[12]	validation_0-rmse:32628.22266
[13]	validation_0-rmse:31314.53906
[14]	validation_0-rmse:30099.68555
[15]	validation_0-rmse:28895.37500


[1]	validation_0-rmse:51431.41016
[2]	validation_0-rmse:49313.28906
[3]	validation_0-rmse:47316.29297
[4]	validation_0-rmse:45267.60156
[5]	validation_0-rmse:43318.59375
[6]	validation_0-rmse:41472.67969
[7]	validation_0-rmse:39836.19922
[8]	validation_0-rmse:38256.68750
[9]	validation_0-rmse:36829.27344
[10]	validation_0-rmse:35447.36328
[11]	validation_0-rmse:34042.76562
[12]	validation_0-rmse:32660.16406
[13]	validation_0-rmse:31344.91602
[14]	validation_0-rmse:30128.48828
[15]	validation_0-rmse:28922.72070
[16]	validation_0-rmse:27892.13672
[17]	validation_0-rmse:26797.45508
[18]	validation_0-rmse:25863.65820
[19]	validation_0-rmse:24833.49805
[20]	validation_0-rmse:23853.24609
[21]	validation_0-rmse:22966.20508
[22]	validation_0-rmse:22090.72461
[23]	validation_0-rmse:21209.73828
[24]	validation_0-rmse:20456.96680
[25]	validation_0-rmse:19694.19727
[26]	validation_0-rmse:18968.46875
[27]	validation_0-rmse:18153.21289
[28]	validation_0-rmse:17576.09766
[29]	validation_0-rmse:16956.

[14]	validation_0-rmse:30099.68555
[15]	validation_0-rmse:28895.37500
[16]	validation_0-rmse:27865.10742
[17]	validation_0-rmse:26771.77148
[18]	validation_0-rmse:25838.25586
[19]	validation_0-rmse:24809.37695
[20]	validation_0-rmse:23830.34375
[21]	validation_0-rmse:22944.89258
[22]	validation_0-rmse:22070.67578
[23]	validation_0-rmse:21190.65625
[24]	validation_0-rmse:20439.26953
[25]	validation_0-rmse:19677.57812
[26]	validation_0-rmse:18952.87891
[27]	validation_0-rmse:18138.33789
[28]	validation_0-rmse:17561.44922
[29]	validation_0-rmse:16943.16406
[30]	validation_0-rmse:16340.83984
[31]	validation_0-rmse:15840.55371
[32]	validation_0-rmse:15267.37500
[33]	validation_0-rmse:14698.50293
[34]	validation_0-rmse:14237.07812
[35]	validation_0-rmse:13791.32910
[36]	validation_0-rmse:13199.28711
[37]	validation_0-rmse:12814.21289
[38]	validation_0-rmse:12371.34082
[39]	validation_0-rmse:11864.51269
[40]	validation_0-rmse:11330.11719
[41]	validation_0-rmse:10943.68359
[42]	validation_0-rm

[27]	validation_0-rmse:18153.21289
[28]	validation_0-rmse:17576.09766
[29]	validation_0-rmse:16956.59180
[30]	validation_0-rmse:16353.09668
[31]	validation_0-rmse:15778.99512
[32]	validation_0-rmse:15198.83398
[33]	validation_0-rmse:14651.25488
[34]	validation_0-rmse:14172.78320
[35]	validation_0-rmse:13745.18750
[36]	validation_0-rmse:13149.94824
[37]	validation_0-rmse:12771.75098
[38]	validation_0-rmse:12319.54004
[39]	validation_0-rmse:11811.15234
[40]	validation_0-rmse:11274.92578
[41]	validation_0-rmse:10887.26758
[42]	validation_0-rmse:10590.44043
[43]	validation_0-rmse:10307.86719
[44]	validation_0-rmse:9875.45898
[45]	validation_0-rmse:9429.17383
[46]	validation_0-rmse:9165.65527
[47]	validation_0-rmse:8754.28320
[48]	validation_0-rmse:8391.45898
[49]	validation_0-rmse:8034.85742
[50]	validation_0-rmse:7674.81494
[51]	validation_0-rmse:7436.95361
[52]	validation_0-rmse:7104.42236
[53]	validation_0-rmse:6807.43457
[54]	validation_0-rmse:6574.57178
[55]	validation_0-rmse:6278.125

[40]	validation_0-rmse:11330.11719
[41]	validation_0-rmse:10943.68359
[42]	validation_0-rmse:10640.91894
[43]	validation_0-rmse:10310.04785
[44]	validation_0-rmse:9880.29883
[45]	validation_0-rmse:9434.91016
[46]	validation_0-rmse:9175.76562
[47]	validation_0-rmse:8765.21387
[48]	validation_0-rmse:8391.52051
[49]	validation_0-rmse:8034.45801
[50]	validation_0-rmse:7675.67969
[51]	validation_0-rmse:7438.22412
[52]	validation_0-rmse:7106.86182
[53]	validation_0-rmse:6841.20898
[54]	validation_0-rmse:6609.18262
[55]	validation_0-rmse:6314.83008
[56]	validation_0-rmse:6057.69873
[57]	validation_0-rmse:5789.63135
[58]	validation_0-rmse:5548.03516
[59]	validation_0-rmse:5396.45068
[60]	validation_0-rmse:5184.71728
[61]	validation_0-rmse:5053.34717
[62]	validation_0-rmse:4865.10693
[63]	validation_0-rmse:4681.98340
[64]	validation_0-rmse:4482.12061
[65]	validation_0-rmse:4294.08057
[66]	validation_0-rmse:4131.04053
[67]	validation_0-rmse:3975.26099
[68]	validation_0-rmse:3828.50513
[69]	valid

...

[1]	validation_0-rmse:42629.01172
[2]	validation_0-rmse:37197.84766
[3]	validation_0-rmse:32982.16406
[4]	validation_0-rmse:29077.73438
[5]	validation_0-rmse:25746.53320
[6]	validation_0-rmse:22621.79492
[7]	validation_0-rmse:20080.05859
[8]	validation_0-rmse:17731.04883
[9]	validation_0-rmse:15885.20312
[10]	validation_0-rmse:13859.71094
[11]	validation_0-rmse:12177.00000
[12]	validation_0-rmse:10931.88574
[13]	validation_0-rmse:9588.52441
[14]	validation_0-rmse:8365.86719
[15]	validation_0-rmse:7211.57568
[16]	validation_0-rmse:6529.25928
[17]	validation_0-rmse:5787.06934
[18]	validation_0-rmse:5084.82861
[19]	validation_0-rmse:4501.33398
[20]	validation_0-rmse:4016.11548
[21]	validation_0-rmse:3535.01294
[22]	validation_0-rmse:3131.19312
[23]	validation_0-rmse:2830.23096
[24]	validation_0-rmse:2595.42627
[25]	validation_0-rmse:2419.43823
[26]	validation_0-rmse:2283.06274
[27]	validation_0-rmse:2203.47607
[28]	validation_0-rmse:2130.64844
[29]	validation_0-rmse:2110.30981
[30]	valida

[6]	validation_0-rmse:22621.79492
[7]	validation_0-rmse:20080.05859
[8]	validation_0-rmse:17731.04883
[9]	validation_0-rmse:15885.20312
[10]	validation_0-rmse:13859.71094
[11]	validation_0-rmse:12177.00000
[12]	validation_0-rmse:10931.88574
[13]	validation_0-rmse:9588.52441
[14]	validation_0-rmse:8365.86719
[15]	validation_0-rmse:7211.57568
[16]	validation_0-rmse:6482.62647
[17]	validation_0-rmse:5739.37891
[18]	validation_0-rmse:5042.71094
[19]	validation_0-rmse:4476.21338
[20]	validation_0-rmse:3905.03296
[21]	validation_0-rmse:3522.50610
[22]	validation_0-rmse:3121.26489
[23]	validation_0-rmse:2818.60376
[24]	validation_0-rmse:2582.60230
[25]	validation_0-rmse:2381.51782
[26]	validation_0-rmse:2249.03174
[27]	validation_0-rmse:2176.12524
[28]	validation_0-rmse:2109.62012
[29]	validation_0-rmse:2083.89990
[30]	validation_0-rmse:2061.58911
[31]	validation_0-rmse:2064.00952
[32]	validation_0-rmse:2059.20874
[33]	validation_0-rmse:2066.27563
[34]	validation_0-rmse:2073.06982
[35]	valida

[12]	validation_0-rmse:10931.88574
[13]	validation_0-rmse:9588.52441
[14]	validation_0-rmse:8365.86719
[15]	validation_0-rmse:7211.57568
[16]	validation_0-rmse:6483.24951
[17]	validation_0-rmse:5740.37402
[18]	validation_0-rmse:5043.53906
[19]	validation_0-rmse:4476.53662
[20]	validation_0-rmse:4008.77759
[21]	validation_0-rmse:3529.79248
[22]	validation_0-rmse:3126.50269
[23]	validation_0-rmse:2824.35669
[24]	validation_0-rmse:2589.00415
[25]	validation_0-rmse:2392.52637
[26]	validation_0-rmse:2260.39356
[27]	validation_0-rmse:2178.36060
[28]	validation_0-rmse:2111.05591
[29]	validation_0-rmse:2100.09814
[30]	validation_0-rmse:2074.12329
[31]	validation_0-rmse:2076.28540
[32]	validation_0-rmse:2067.39868
[33]	validation_0-rmse:2064.94873
[34]	validation_0-rmse:2072.65308
[35]	validation_0-rmse:2083.88257
[36]	validation_0-rmse:2099.19409
[37]	validation_0-rmse:2105.91870
[38]	validation_0-rmse:2123.77856
[39]	validation_0-rmse:2132.42700
[40]	validation_0-rmse:2131.61914
[41]	validati

[17]	validation_0-rmse:5740.37402
[18]	validation_0-rmse:5043.53906
[19]	validation_0-rmse:4476.53662
[20]	validation_0-rmse:4008.77759
[21]	validation_0-rmse:3529.79248
[22]	validation_0-rmse:3128.13574
[23]	validation_0-rmse:2825.64624
[24]	validation_0-rmse:2589.99438
[25]	validation_0-rmse:2394.96118
[26]	validation_0-rmse:2262.23047
[27]	validation_0-rmse:2184.96167
[28]	validation_0-rmse:2117.21558
[29]	validation_0-rmse:2089.53857
[30]	validation_0-rmse:2062.46362
[31]	validation_0-rmse:2047.36182
[32]	validation_0-rmse:2046.61572
[33]	validation_0-rmse:2053.70508
[34]	validation_0-rmse:2061.35278
[35]	validation_0-rmse:2072.85840
[36]	validation_0-rmse:2085.90527
[37]	validation_0-rmse:2092.34668
[38]	validation_0-rmse:2108.85644
[39]	validation_0-rmse:2116.07715
[40]	validation_0-rmse:2116.33667
[41]	validation_0-rmse:2141.19727
[42]	validation_0-rmse:2147.84790
Stopping. Best iteration:
[32]	validation_0-rmse:2046.61572

[18:35:27] WARNING: C:\Users\Administrator\workspace\xg

[20]	validation_0-rmse:4008.77759
[21]	validation_0-rmse:3529.79248
[22]	validation_0-rmse:3128.13574
[23]	validation_0-rmse:2825.64624
[24]	validation_0-rmse:2589.99438
[25]	validation_0-rmse:2394.00000
[26]	validation_0-rmse:2261.51856
[27]	validation_0-rmse:2186.43530
[28]	validation_0-rmse:2118.41968
[29]	validation_0-rmse:2085.87036
[30]	validation_0-rmse:2059.27197
[31]	validation_0-rmse:2061.09912
[32]	validation_0-rmse:2054.04199
[33]	validation_0-rmse:2067.09595
[34]	validation_0-rmse:2074.31885
[35]	validation_0-rmse:2080.49658
[36]	validation_0-rmse:2090.08301
[37]	validation_0-rmse:2094.78149
[38]	validation_0-rmse:2106.69775
[39]	validation_0-rmse:2113.35083
[40]	validation_0-rmse:2124.13696
[41]	validation_0-rmse:2126.78320
[42]	validation_0-rmse:2132.95508
Stopping. Best iteration:
[32]	validation_0-rmse:2054.04199

[18:35:28] WARNING: C:\Users\Administrator\workspace\xgboost-win64_release_1.2.0\src\learner.cc:516: 
Parameters: { verbose } might not be used.

  This may 

In [20]:
model = xgb.XGBRegressor(**clf.best_params_, objective='reg:squarederror')
model.fit(x_train_trans, y_train, verbose=False, early_stopping_rounds=10, eval_set=eval_set)

y_pred = model.predict(x_train_trans)

# Train Set RMSE Computation
rmse = np.sqrt(MSE(y_train, y_pred))
print("Test set RMSE: % f" %(rmse))

y_pred = model.predict(x_test_trans)

# Test Set RMSE Computation
rmse = np.sqrt(MSE(y_test, y_pred))
print("Test set RMSE: % f" %(rmse))

Test set RMSE:  493.963326
Test set RMSE:  3443.519868


In [21]:
# without sentiments 
y_train_pred = model.predict(x_train_trans)
y_validation_pred = model.predict(x_validation_trans)
y_test_pred = model.predict(x_test_trans)

concat = np.concatenate((y_train_pred, y_validation_pred, y_test_pred))
pd.DataFrame(concat).to_csv(r'C:\Users\Yi Hao\Desktop\XGBoost_regression_without_sentiment.csv')